<a href="https://colab.research.google.com/github/SalahAdDin/ThesisObjectDetectionDeepLearning/blob/master/YOLOv3.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

# YOLO Colab Implementation

We are implementing **YOLOv3** in **Colab**; we will test this with all different datasets in order to compare.

I used this [blog](https://www.learnopencv.com/training-yolov3-deep-learning-based-custom-object-detector/) as base to complete this work.

## Setup

Installing requirements to compile **YOLO Darknet**:

In [0]:
!lsb_release -a && free -m && nvcc --version && gcc -v && lscpu

No LSB modules are available.
Distributor ID:	Ubuntu
Description:	Ubuntu 18.04.3 LTS
Release:	18.04
Codename:	bionic
              total        used        free      shared  buff/cache   available
Mem:          13021         585       10274           0        2160       12158
Swap:             0           0           0
nvcc: NVIDIA (R) Cuda compiler driver
Copyright (c) 2005-2019 NVIDIA Corporation
Built on Sun_Jul_28_19:07:16_PDT_2019
Cuda compilation tools, release 10.1, V10.1.243
Using built-in specs.
COLLECT_GCC=gcc
COLLECT_LTO_WRAPPER=/usr/lib/gcc/x86_64-linux-gnu/7/lto-wrapper
OFFLOAD_TARGET_NAMES=nvptx-none
OFFLOAD_TARGET_DEFAULT=1
Target: x86_64-linux-gnu
Configured with: ../src/configure -v --with-pkgversion='Ubuntu 7.5.0-3ubuntu1~18.04' --with-bugurl=file:///usr/share/doc/gcc-7/README.Bugs --enable-languages=c,ada,c++,go,brig,d,fortran,objc,obj-c++ --prefix=/usr --with-gcc-major-version-only --program-suffix=-7 --program-prefix=x86_64-linux-gnu- --enable-shared --enable-linke

In [0]:
import cv2
cv2.__version__

'4.1.2'

In [0]:
!dpkg --configure -a

In [0]:
!apt install libomp-dev -y --no-install-recommends libnvinfer6=6.0.1-1+cuda10.0 \
    libnvinfer-dev=6.0.1-1+cuda10.0 \
    libnvinfer-plugin6=6.0.1-1+cuda10.0

Reading package lists... Done
Building dependency tree       
Reading state information... Done
The following additional packages will be installed:
  libomp5
Suggested packages:
  libomp-doc
The following NEW packages will be installed:
  libnvinfer-dev libnvinfer-plugin6 libnvinfer6 libomp-dev libomp5
0 upgraded, 5 newly installed, 0 to remove and 29 not upgraded.
Need to get 136 MB of archives.
After this operation, 461 MB of additional disk space will be used.
Get:1 https://developer.download.nvidia.com/compute/machine-learning/repos/ubuntu1804/x86_64  libnvinfer6 6.0.1-1+cuda10.0 [66.8 MB]
Get:2 http://archive.ubuntu.com/ubuntu bionic/universe amd64 libomp5 amd64 5.0.1-1 [234 kB]
Get:3 http://archive.ubuntu.com/ubuntu bionic/universe amd64 libomp-dev amd64 5.0.1-1 [5,088 B]
Get:4 https://developer.download.nvidia.com/compute/machine-learning/repos/ubuntu1804/x86_64  libnvinfer-dev 6.0.1-1+cuda10.0 [67.3 MB]
Get:5 https://developer.download.nvidia.com/compute/machine-learning/repos

In [0]:
!nvcc --version
!nvidia-smi

nvcc: NVIDIA (R) Cuda compiler driver
Copyright (c) 2005-2019 NVIDIA Corporation
Built on Sun_Jul_28_19:07:16_PDT_2019
Cuda compilation tools, release 10.1, V10.1.243
Sun May 10 17:43:40 2020       
+-----------------------------------------------------------------------------+
| NVIDIA-SMI 440.82       Driver Version: 418.67       CUDA Version: 10.1     |
|-------------------------------+----------------------+----------------------+
| GPU  Name        Persistence-M| Bus-Id        Disp.A | Volatile Uncorr. ECC |
| Fan  Temp  Perf  Pwr:Usage/Cap|         Memory-Usage | GPU-Util  Compute M. |
|===============================+======================+======================|
|   0  Tesla P100-PCIE...  Off  | 00000000:00:04.0 Off |                    0 |
| N/A   45C    P0    30W / 250W |      0MiB / 16280MiB |      0%      Default |
+-------------------------------+----------------------+----------------------+
                                                                               
+

In [0]:
gpu_info = !nvidia-smi
gpu_info = '\n'.join(gpu_info)
if gpu_info.find('failed') >= 0:
  print('Select the Runtime > "Change runtime type" menu to enable a GPU accelerator, ')
  print('and then re-execute this cell.')
else:
  print(gpu_info)

Sun May 10 17:43:42 2020       
+-----------------------------------------------------------------------------+
| NVIDIA-SMI 440.82       Driver Version: 418.67       CUDA Version: 10.1     |
|-------------------------------+----------------------+----------------------+
| GPU  Name        Persistence-M| Bus-Id        Disp.A | Volatile Uncorr. ECC |
| Fan  Temp  Perf  Pwr:Usage/Cap|         Memory-Usage | GPU-Util  Compute M. |
|===============================+======================+======================|
|   0  Tesla P100-PCIE...  Off  | 00000000:00:04.0 Off |                    0 |
| N/A   45C    P0    30W / 250W |      0MiB / 16280MiB |      0%      Default |
+-------------------------------+----------------------+----------------------+
                                                                               
+-----------------------------------------------------------------------------+
| Processes:                                                       GPU Memory |
|  GPU  

In [0]:
!pip install -U vtk gdown #numpy

     |████████████████████████████████| 48.9MB 65kB/s 
  Installing build dependencies ... done
  Getting requirements to build wheel ... done
    Preparing wheel metadata ... done
  Created wheel for gdown: filename=gdown-3.11.0-cp36-none-any.whl size=9619 sha256=fca86ecb0633b02e425aa15144daf2d79fd4cd389fce36987d7ca1f12e7197b5
  Stored in directory: /root/.cache/pip/wheels/19/a6/67/ebb80360fc57bb0ddd5da77f57b275084cd8838bf7d5b91685
Successfully built gdown
  Found existing installation: gdown 3.6.4
    Uninstalling gdown-3.6.4:
      Successfully uninstalled gdown-3.6.4


Cloning the repository from the useful fork:

In [0]:
!git clone https://github.com/AlexeyAB/darknet.git

Cloning into 'darknet'...
remote: Enumerating objects: 71, done.
remote: Counting objects: 100% (71/71), done.
remote: Compressing objects: 100% (43/43), done.
remote: Total 13428 (delta 37), reused 47 (delta 28), pack-reused 13357
Receiving objects: 100% (13428/13428), 12.11 MiB | 20.64 MiB/s, done.
Resolving deltas: 100% (9158/9158), done.


In [0]:
cd darknet/

/content/darknet


We need to define some parameters before to compile:

In [0]:
!sed -i 's/GPU=0/GPU=1/g' Makefile
!sed -i 's/CUDNN=0/CUDNN=1/g' Makefile
!sed -i 's/CUDNN_HALF=0/CUDNN_HALF=1/g' Makefile
!sed -i 's/OPENCV=0/OPENCV=1/g' Makefile
# !sed -i 's/OPENMP=0/OPENMP=1/g' Makefile

In [0]:
!cat Makefile

GPU=1
CUDNN=1
CUDNN_HALF=1
OPENCV=1
AVX=0
OPENMP=0
LIBSO=0
ZED_CAMERA=0 # ZED SDK 3.0 and above
ZED_CAMERA_v2_8=0 # ZED SDK 2.X

# set GPU=1 and CUDNN=1 to speedup on GPU
# set CUDNN_HALF=1 to further speedup 3 x times (Mixed-precision on Tensor Cores) GPU: Volta, Xavier, Turing and higher
# set AVX=1 and OPENMP=1 to speedup on CPU (if error occurs then set AVX=0)

USE_CPP=0
DEBUG=0

ARCH= -gencode arch=compute_30,code=sm_30 \
      -gencode arch=compute_35,code=sm_35 \
      -gencode arch=compute_50,code=[sm_50,compute_50] \
      -gencode arch=compute_52,code=[sm_52,compute_52] \
	    -gencode arch=compute_61,code=[sm_61,compute_61]

OS := $(shell uname)

# Tesla V100
# ARCH= -gencode arch=compute_70,code=[sm_70,compute_70]

# GeForce RTX 2080 Ti, RTX 2080, RTX 2070, Quadro RTX 8000, Quadro RTX 6000, Quadro RTX 5000, Tesla T4, XNOR Tensor Cores
# ARCH= -gencode arch=compute_75,code=[sm_75,compute_75]

# Jetson XAVIER
# ARCH= -gencode arch=compute_72,code=[sm_72,compute_72]

# GTX 108

Now, building **darknet**:

In [0]:
!make

mkdir -p ./obj/
mkdir -p backup
chmod +x *.sh
g++ -std=c++11 -std=c++11 -Iinclude/ -I3rdparty/stb/include -DOPENCV `pkg-config --cflags opencv4 2> /dev/null || pkg-config --cflags opencv` -DGPU -I/usr/local/cuda/include/ -DCUDNN -DCUDNN_HALF -Wall -Wfatal-errors -Wno-unused-result -Wno-unknown-pragmas -fPIC -Ofast -DOPENCV -DGPU -DCUDNN -I/usr/local/cudnn/include -DCUDNN_HALF -c ./src/image_opencv.cpp -o obj/image_opencv.o
./src/image_opencv.cpp: In function ‘void draw_detections_cv_v3(void**, detection*, int, float, char**, image**, int, int)’:
./src/image_opencv.cpp:910:23: warning: variable ‘rgb’ set but not used [-Wunused-but-set-variable]
                 float rgb[3];
                       ^~~
./src/image_opencv.cpp: In function ‘void cv_draw_object(image, float*, int, int, int*, float*, int*, int, char**)’:
./src/image_opencv.cpp:1391:14: warning: unused variable ‘buff’ [-Wunused-variable]
         char buff[100];
              ^~~~
./src/image_opencv.cpp:1367:9: warning: unuse

## Making Dataset
Download from Drive training dataset.

In [0]:
import os
import shutil
import time
import zipfile

from google.colab import drive
from google.colab import files

#### OPTIONAL: EXPORT TRAINED MODEL TO DRIVE ####
drive.mount('/content/gdrive', force_remount=False)

Go to this URL in a browser: https://accounts.google.com/o/oauth2/auth?client_id=947318989803-6bn6qk8qdgf4n4g3pfee6491hc0brc4i.apps.googleusercontent.com&redirect_uri=urn%3aietf%3awg%3aoauth%3a2.0%3aoob&response_type=code&scope=email%20https%3a%2f%2fwww.googleapis.com%2fauth%2fdocs.test%20https%3a%2f%2fwww.googleapis.com%2fauth%2fdrive%20https%3a%2f%2fwww.googleapis.com%2fauth%2fdrive.photos.readonly%20https%3a%2f%2fwww.googleapis.com%2fauth%2fpeopleapi.readonly

Enter your authorization code:
··········
Mounted at /content/gdrive


In [0]:
DATASET_DIR = 'dataset'

In [0]:
os.makedirs(DATASET_DIR, exist_ok=True)

### MangoYOLO

In [0]:
file_name = 'MangoYOLO.zip'

!gdown https://drive.google.com/uc?id=1iZbPYck5BuIsZ9GQCSHI4LlqMyxmCrP9
# !gdown https://drive.google.com/uc?id=1oDOJFuhuixkx1ePu1G1HqSeKXhuhfA-B
print('Download completed!')

with zipfile.ZipFile(file_name, 'r') as zip_ref:
  zip_ref.extractall(DATASET_DIR)
os.remove(file_name)
print('Extract completed!')

Downloading...
From: https://drive.google.com/uc?id=1iZbPYck5BuIsZ9GQCSHI4LlqMyxmCrP9
To: /content/darknet/MangoYOLO.zip
163MB [00:01, 96.3MB/s]
Download completed!
Extract completed!


### ACFR Multifruit

In [0]:
file_name = 'acfr-fruit-dataset.zip'

!gdown https://drive.google.com/uc?id=1d0DXYLCAZHrL4RudWP_4Gty46MSRH4_G
print('Download completed!')

with zipfile.ZipFile(file_name, 'r') as zip_ref:
  zip_ref.extractall(DATASET_DIR)
os.remove(file_name)
print('Extract completed!')

Downloading...
From: https://drive.google.com/uc?id=1d0DXYLCAZHrL4RudWP_4Gty46MSRH4_G
To: /content/darknet/acfr-fruit-dataset.zip
2.23GB [00:26, 84.4MB/s]
Download completed!
Extract completed!


### WGISD(grapes)

In [0]:
%cd dataset

/content/darknet/dataset


In [0]:
!git clone https://github.com/thsant/wgisd.git

Cloning into 'wgisd'...
remote: Enumerating objects: 3400, done.
remote: Total 3400 (delta 0), reused 0 (delta 0), pack-reused 3400
Receiving objects: 100% (3400/3400), 1.33 GiB | 37.08 MiB/s, done.
Resolving deltas: 100% (323/323), done.
Checking out files: 100% (1045/1045), done.


In [0]:
!echo "m" > m.names
!echo "uva" > uva.names
!echo "almond" > almond.names
!echo "apple" > apple.names
!echo "mango" > mango.names

Get the label file generator for **PASCAL VOC**:

In [0]:
!gdown https://drive.google.com/uc?id=1uuREbiUvOgEN5_L454MX1viTmVWNjBHs
!gdown https://drive.google.com/uc?id=1qbr5ogr180muuZPidrqge7lQti5ESE6P
print('Extract completed!')

Downloading...
From: https://drive.google.com/uc?id=1uuREbiUvOgEN5_L454MX1viTmVWNjBHs
To: /content/darknet/dataset/voc_label.py
100% 2.53k/2.53k [00:00<00:00, 5.10MB/s]
Downloading...
From: https://drive.google.com/uc?id=1qbr5ogr180muuZPidrqge7lQti5ESE6P
To: /content/darknet/dataset/yolov3-voc.cfg
100% 8.55k/8.55k [00:00<00:00, 19.0MB/s]
Extract completed!


Generating labels for training YOLO:

In [0]:
!python voc_label.py -p /content/darknet/dataset/VOCDevkit/VOC2007

In [0]:
!python voc_label.py -ie .png -p /content/darknet/dataset/acfr-fruit-dataset/almonds

In [0]:
!python voc_label.py -ie .png -p /content/darknet/dataset/acfr-fruit-dataset/apples

In [0]:
!python voc_label.py -ie .png -p /content/darknet/dataset/acfr-fruit-dataset/mangoes

In [0]:
# We need to put the correct image path for each set in WGISD dataset
  folder_path = '/content/darknet/dataset/wgisd'
  image_folder_path = folder_path + "/data/"

  sets = ['train', 'test']

  for image_set in sets:
      image_ids = open(os.path.join(os.path.abspath(
          folder_path), '{}.txt'.format(image_set))).read().strip().split()
      list_file = open(os.path.join(os.path.abspath(
          folder_path), '{}.txt'.format(image_set)), 'w')
      for image_id in image_ids:
          list_file.write(os.path.join(os.path.abspath(
              image_folder_path), '{}.jpg\n'.format(image_id)))
      list_file.close()

Now, we have to create the data file for each dataset:



In [0]:
# !sed -i 's/classes= 20/classes = 21/g' ../cfg/voc.data
# !sed -i 's|train  = /home/pjreddie/data/voc/train.txt|train = dataset/2007_train.txt|g' ../cfg/voc.data
# !sed -i 's|valid  = /home/pjreddie/data/voc/2007_test.txt|valid = dataset/2007_val.txt|g' ../cfg/voc.data
# !sed -i 's|names = data/voc.names|names = dataset/voc.names|g' ../cfg/voc.data
# !sed -i 's|backup = /home/pjreddie/backup/|backup = backup|g' ../cfg/voc.data
# !cp ../data/voc.names ../dataset
# !sed -i -e '$a\M' ../dataset/voc.names

In [0]:
# Mango YOLO
!echo $'classes= 1\ntrain = /content/darknet/dataset/VOCDevkit/VOC2007/train.txt\nvalid = /content/darknet/dataset/VOCDevkit/VOC2007/val.txt\nnames = /content/darknet/dataset/m.names\nbackup = /content/darknet/backup/' > m.data

In [0]:
# ACFR - Almonds
!echo $'classes= 1\ntrain = /content/darknet/dataset/acfr-fruit-dataset/almonds/train.txt\nvalid = /content/darknet/dataset/acfr-fruit-dataset/almonds/val.txt\nnames = /content/darknet/dataset/almond.names\nbackup = /content/darknet/backup/' > almond.data

In [0]:
# ACFR - Apples
!echo $'classes= 1\ntrain = /content/darknet/dataset/acfr-fruit-dataset/apples/train.txt\nvalid = /content/darknet/dataset/acfr-fruit-dataset/apples/val.txt\nnames = /content/darknet/dataset/apple.names\nbackup = /content/darknet/backup/' > apple.data

In [0]:
# ACFR - Mangoes
!echo $'classes= 1\ntrain = /content/darknet/dataset/acfr-fruit-dataset/mangoes/train.txt\nvalid = /content/darknet/dataset/acfr-fruit-dataset/mangoes/val.txt\nnames = /content/darknet/dataset/mango.names\nbackup = /content/darknet/backup/' > mango.data

In [0]:
# WGISD
!echo $'classes= 1\ntrain = /content/darknet/dataset/wgisd/train.txt\nvalid = /content/darknet/dataset/wgisd/test.txt\nnames = /content/darknet/dataset/uva.names\nbackup = /content/darknet/backup/' > uva.data

Finally, before to train it, we will review our setup:

In [0]:
%cd ../

/content/darknet


In [0]:
!cat dataset/yolov3-voc.cfg

# Based on cfg/yolov3-voc.cfg

[net]
# Testing
# batch=1
# subdivisions=1
# Training
batch=64
subdivisions=16
width=416
height=416
channels=3
momentum=0.9
decay=0.0005
angle=0
saturation = 1.5
exposure = 1.5
hue=.1

learning_rate=0.001
burn_in=400
max_batches=5200
policy=steps
steps=3800
scales=.1

[convolutional]
batch_normalize=1
filters=32
size=3
stride=1
pad=1
activation=leaky

# Downsample

[convolutional]
batch_normalize=1
filters=64
size=3
stride=2
pad=1
activation=leaky

[convolutional]
batch_normalize=1
filters=32
size=1
stride=1
pad=1
activation=leaky

[convolutional]
batch_normalize=1
filters=64
size=3
stride=1
pad=1
activation=leaky

[shortcut]
from=-3
activation=linear

# Downsample

[convolutional]
batch_normalize=1
filters=128
size=3
stride=2
pad=1
activation=leaky

[convolutional]
batch_normalize=1
filters=64
size=1
stride=1
pad=1
activation=leaky

[convolutional]
batch_normalize=1
filters=128
size=3
stride=1
pad=1
activation=leaky

[shortcut]
from=-3
activation=linear


In [0]:
!cat dataset/m.data && cat dataset/uva.data && cat dataset/almond.data && cat dataset/apple.data && cat dataset/mango.data

classes= 1
train = /content/darknet/dataset/VOCDevkit/VOC2007/train.txt
valid = /content/darknet/dataset/VOCDevkit/VOC2007/val.txt
names = /content/darknet/dataset/m.names
backup = /content/darknet/backup/
classes= 1
train = /content/darknet/dataset/wgisd/train.txt
valid = /content/darknet/dataset/wgisd/test.txt
names = /content/darknet/dataset/uva.names
backup = /content/darknet/backup/
classes= 1
train = /content/darknet/dataset/acfr-fruit-dataset/almonds/train.txt
valid = /content/darknet/dataset/acfr-fruit-dataset/almonds/val.txt
names = /content/darknet/dataset/almond.names
backup = /content/darknet/backup/
classes= 1
train = /content/darknet/dataset/acfr-fruit-dataset/apples/train.txt
valid = /content/darknet/dataset/acfr-fruit-dataset/apples/val.txt
names = /content/darknet/dataset/apple.names
backup = /content/darknet/backup/
classes= 1
train = /content/darknet/dataset/acfr-fruit-dataset/mangoes/train.txt
valid = /content/darknet/dataset/acfr-fruit-dataset/mangoes/val.txt
names

In [0]:
!cat dataset/m.names && cat dataset/uva.names && cat dataset/almond.names && cat dataset/apple.names && cat dataset/mango.names

m
uva
almond
apple
mango


## Training

Now, we will train **YOLOv3** with the different datasets; we will use transfer learning in order to make this process faster.

Setting batch size and subdivisions, also we set the data for training **VOC**:

Downloading pretrained models:

In [0]:
!mkdir /content/models
!wget https://pjreddie.com/media/files/darknet53.conv.74

--2020-05-10 17:51:09--  https://pjreddie.com/media/files/darknet53.conv.74
Resolving pjreddie.com (pjreddie.com)... 128.208.4.108
Connecting to pjreddie.com (pjreddie.com)|128.208.4.108|:443... connected.
HTTP request sent, awaiting response... 200 OK
Length: 162482580 (155M) [application/octet-stream]
Saving to: ‘darknet53.conv.74’

darknet53.conv.74   100%[===================>] 154.96M  1.86MB/s    in 96s     

2020-05-10 17:52:46 (1.61 MB/s) - ‘darknet53.conv.74’ saved [162482580/162482580]



In [0]:
DRIVE_DIR = '/content/gdrive/My Drive/Colab Notebooks/'

Training the model:

In [0]:
# WGISD
start = time.time()
!./darknet detector train dataset/uva.data dataset/yolov3-voc.cfg darknet53.conv.74 -dont_show > train_wgisd.log
final = time.time() - start
print("Training time in seconds: ", final)
print("Training time in hours: ", final/(60*60))
!mv /content/darknet/backup/yolov3-voc_final.weights /content/models/yolov3-wgisd.weights
!rm -rf backup/*

shutil.copy('/content/models/yolov3-wgisd.weights', DRIVE_DIR)
shutil.copy('/content/darknet/train_wgisd.log', DRIVE_DIR)

Se han truncado las últimas 5000 líneas del flujo de salida.
v3 (giou loss, Normalizer: (iou: 0.30, cls: 1.00) Region 94 Avg (IOU: 0.913309, GIOU: 0.912501), Class: 0.999170, Obj: 0.911169, No Obj: 0.004959, .5R: 1.000000, .75R: 0.968750, count: 32, class_loss = 0.837643, iou_loss = 490.203003, total_loss = 491.040649 
v3 (giou loss, Normalizer: (iou: 0.30, cls: 1.00) Region 106 Avg (IOU: 0.872340, GIOU: 0.870452), Class: 0.986758, Obj: 0.437940, No Obj: 0.000322, .5R: 1.000000, .75R: 0.970588, count: 34, class_loss = 4.824662, iou_loss = 2153.309082, total_loss = 2158.133789 
v3 (giou loss, Normalizer: (iou: 0.30, cls: 1.00) Region 82 Avg (IOU: 0.000000, GIOU: 0.000000), Class: 0.000000, Obj: 0.000000, No Obj: 0.000005, .5R: 0.000000, .75R: 0.000000, count: 1, class_loss = 0.000011, iou_loss = 0.000000, total_loss = 0.000011 
v3 (giou loss, Normalizer: (iou: 0.30, cls: 1.00) Region 94 Avg (IOU: 0.915438, GIOU: 0.914210), Class: 0.998982, Obj: 0.938551, No Obj: 0.006561, .5R: 1.000000,

'/content/gdrive/My Drive/Colab Notebooks/train_wgisd.log'

In [0]:
# ACFR - Almonds
start = time.time()
!./darknet detector train dataset/almond.data dataset/yolov3-voc.cfg darknet53.conv.74 -dont_show > train_acfr_almond.log
final = time.time() - start
print("Training time in seconds: ", final)
print("Training time in hours: ", final/(60*60))

!mv /content/darknet/backup/yolov3-voc_final.weights /content/models/yolov3-acfr-almond.weights
!rm -rf backup/*

shutil.copy('/content/models/yolov3-acfr-almond.weights', DRIVE_DIR)
shutil.copy('/content/darknet/train_acfr_almond.log', DRIVE_DIR)

Se han truncado las últimas 5000 líneas del flujo de salida.
v3 (giou loss, Normalizer: (iou: 0.30, cls: 1.00) Region 94 Avg (IOU: 0.913993, GIOU: 0.913418), Class: 0.996066, Obj: 0.839188, No Obj: 0.003992, .5R: 1.000000, .75R: 1.000000, count: 20, class_loss = 0.747919, iou_loss = 191.758545, total_loss = 192.506470 
v3 (giou loss, Normalizer: (iou: 0.30, cls: 1.00) Region 106 Avg (IOU: 0.898382, GIOU: 0.897201), Class: 0.999100, Obj: 0.343509, No Obj: 0.000115, .5R: 1.000000, .75R: 1.000000, count: 9, class_loss = 1.568624, iou_loss = 204.414490, total_loss = 205.983109 
v3 (giou loss, Normalizer: (iou: 0.30, cls: 1.00) Region 82 Avg (IOU: 0.000000, GIOU: 0.000000), Class: 0.000000, Obj: 0.000000, No Obj: 0.000001, .5R: 0.000000, .75R: 0.000000, count: 1, class_loss = 0.000000, iou_loss = 0.000000, total_loss = 0.000000 
v3 (giou loss, Normalizer: (iou: 0.30, cls: 1.00) Region 94 Avg (IOU: 0.942959, GIOU: 0.942959), Class: 0.999506, Obj: 0.468813, No Obj: 0.000279, .5R: 1.000000, .7

'/content/gdrive/My Drive/Colab Notebooks/train_acfr_almond.log'

In [0]:
# ACFR - Apples
start = time.time()
!./darknet detector train dataset/apple.data dataset/yolov3-voc.cfg darknet53.conv.74 -dont_show > train_acfr_apple.log
final = time.time() - start
print("Training time in seconds: ", final)
print("Training time in hours: ", final/(60*60))


!mv /content/darknet/backup/yolov3-voc_final.weights /content/models/yolov3-acfr-apple.weights
!rm -rf backup/*

shutil.copy('/content/models/yolov3-acfr-apple.weights', DRIVE_DIR)
shutil.copy('/content/darknet/train_acfr_apple.log', DRIVE_DIR)

Se han truncado las últimas 5000 líneas del flujo de salida.
v3 (giou loss, Normalizer: (iou: 0.30, cls: 1.00) Region 82 Avg (IOU: 0.000000, GIOU: 0.000000), Class: 0.000000, Obj: 0.000000, No Obj: 0.072113, .5R: 0.000000, .75R: 0.000000, count: 1, class_loss = 4.896417, iou_loss = 0.000000, total_loss = 4.896417 
v3 (giou loss, Normalizer: (iou: 0.30, cls: 1.00) Region 94 Avg (IOU: 0.441676, GIOU: 0.348257), Class: 0.532075, Obj: 0.025180, No Obj: 0.026901, .5R: 0.357143, .75R: 0.000000, count: 14, class_loss = 7.101362, iou_loss = 58.958874, total_loss = 66.060234 
v3 (giou loss, Normalizer: (iou: 0.30, cls: 1.00) Region 106 Avg (IOU: 0.000000, GIOU: 0.000000), Class: 0.000000, Obj: 0.000000, No Obj: 0.000559, .5R: 0.000000, .75R: 0.000000, count: 1, class_loss = 0.033370, iou_loss = 0.000000, total_loss = 0.033370 
v3 (giou loss, Normalizer: (iou: 0.30, cls: 1.00) Region 82 Avg (IOU: 0.000000, GIOU: 0.000000), Class: 0.000000, Obj: 0.000000, No Obj: 0.073405, .5R: 0.000000, .75R: 0.

In [0]:
# ACFR - Mangoes
start = time.time()
!./darknet detector train dataset/mango.data dataset/yolov3-voc.cfg darknet53.conv.74 -dont_show > train_acfr_mango.log
final = time.time() - start
print("Training time in seconds: ", final)
print("Training time in hours: ", final/(60*60))

!mv /content/darknet/backup/yolov3-voc_final.weights /content/models/yolov3-acfr-mango.weights
!rm -rf backup/*

shutil.copy('/content/models/yolov3-acfr-mango.weights', DRIVE_DIR)
shutil.copy('/content/darknet/train_acfr_mango.log', DRIVE_DIR)

Se han truncado las últimas 5000 líneas del flujo de salida.
v3 (giou loss, Normalizer: (iou: 0.30, cls: 1.00) Region 94 Avg (IOU: 0.897154, GIOU: 0.896211), Class: 0.994420, Obj: 0.687088, No Obj: 0.000439, .5R: 1.000000, .75R: 1.000000, count: 8, class_loss = 0.304881, iou_loss = 297.308105, total_loss = 297.612976 
v3 (giou loss, Normalizer: (iou: 0.30, cls: 1.00) Region 106 Avg (IOU: 0.889205, GIOU: 0.888625), Class: 0.991260, Obj: 0.420304, No Obj: 0.000031, .5R: 1.000000, .75R: 1.000000, count: 7, class_loss = 0.836490, iou_loss = 501.990631, total_loss = 502.827118 
v3 (giou loss, Normalizer: (iou: 0.30, cls: 1.00) Region 82 Avg (IOU: 0.686534, GIOU: 0.654762), Class: 0.989193, Obj: 0.357007, No Obj: 0.000187, .5R: 1.000000, .75R: 0.000000, count: 1, class_loss = 0.112821, iou_loss = 3.126610, total_loss = 3.239431 
v3 (giou loss, Normalizer: (iou: 0.30, cls: 1.00) Region 94 Avg (IOU: 0.853486, GIOU: 0.850122), Class: 0.994534, Obj: 0.512952, No Obj: 0.000301, .5R: 1.000000, .75

'/content/gdrive/My Drive/Colab Notebooks/train_acfr_mango.log'

In [38]:
# Mango YOLO
start = time.time()
!./darknet detector train dataset/m.data dataset/yolov3-voc.cfg darknet53.conv.74 -dont_show > train_mango_yolo.log
final = time.time() - start
print("Training time in seconds: ", final)
print("Training time in hours: ", final/(60*60))

!mv /content/darknet/backup/yolov3-voc_final.weights /content/models/yolov3-mango.weights
!rm -rf backup/*

shutil.copy('/content/models/yolov3-mango.weights', DRIVE_DIR)
shutil.copy('/content/darknet/train_mango_yolo.log', DRIVE_DIR)

Se truncaron las últimas líneas 5000 del resultado de transmisión.
v3 (giou loss, Normalizer: (iou: 0.30, cls: 1.00) Region 82 Avg (IOU: 0.000000, GIOU: 0.000000), Class: 0.000000, Obj: 0.000000, No Obj: 0.000003, .5R: 0.000000, .75R: 0.000000, count: 1, class_loss = 0.000000, iou_loss = 0.000000, total_loss = 0.000000 
v3 (giou loss, Normalizer: (iou: 0.30, cls: 1.00) Region 94 Avg (IOU: 0.000000, GIOU: 0.000000), Class: 0.000000, Obj: 0.000000, No Obj: 0.000334, .5R: 0.000000, .75R: 0.000000, count: 1, class_loss = 0.219361, iou_loss = 0.000000, total_loss = 0.219361 
v3 (giou loss, Normalizer: (iou: 0.30, cls: 1.00) Region 106 Avg (IOU: 0.815386, GIOU: 0.810041), Class: 0.979210, Obj: 0.382713, No Obj: 0.000643, .5R: 1.000000, .75R: 0.782609, count: 46, class_loss = 7.464297, iou_loss = 1665.791748, total_loss = 1673.256104 
v3 (giou loss, Normalizer: (iou: 0.30, cls: 1.00) Region 82 Avg (IOU: 0.000000, GIOU: 0.000000), Class: 0.000000, Obj: 0.000000, No Obj: 0.000002, .5R: 0.000000

In [0]:
#### OPTIONAL: EXPORT TRAINED MODEL TO DRIVE ####
# drive.mount('/content/gdrive')
"""
COLAB_MODELS = [
               '/content/models/yolov3-mango.weights',
               '/content/models/yolov3-acfr-almond.weights',
               '/content/models/yolov3-acfr-apple.weights',
               '/content/models/yolov3-acfr-mango.weights', 
               '/content/models/yolov3-wgisd.weights'
               ]
COLAB_LOGS = [
              '/content/darknet/train_mango_yolo.log',
              '/content/darknet/train_acfr_almond.log',
              '/content/darknet/train_acfr_apple.log',
              '/content/darknet/train_acfr_mango.log', 
              '/content/darknet/train_wgisd.log'
              ]

for model in COLAB_MODELS:
  try:
    shutil.copy(model, DRIVE_DIR)
  except:
    print('{} does not exist'.format(model))
for log in COLAB_LOGS:
  try:
    shutil.copy(log, DRIVE_DIR)
  except:
    print('{} does not exist'.format(log))
"""

## Getting trained models

It is optional if we already have the trained models.

In [0]:

%cd /content/models
# !gdown https://drive.google.com/uc?id=1V7fxxER2J4xlRBd5nPurWYQpI-GIfUWz
# !gdown https://drive.google.com/uc?id=1OIuE5oj-R7GPDoKN8W3tKnw8733KgFDI
!gdown https://drive.google.com/uc?id=1--2NDbfVPfd2_KJDbcDN83Kij8J8qowH
# !gdown https://drive.google.com/uc?id=1rvsBrJFjKIDfybNvNvnJI-yw8SVp9SrT
# !gdown https://drive.google.com/uc?id=1glvdm85qN4yGxXsgNRTlMT4ESa_s5LCJ
print('Download completed!')
%cd /content/darknet/

[Errno 2] No such file or directory: '/content/models'
/content/darknet
Downloading...
From: https://drive.google.com/uc?id=1--2NDbfVPfd2_KJDbcDN83Kij8J8qowH
To: /content/darknet/yolov3-acfr-apple.weights
246MB [00:17, 14.2MB/s]
Download completed!
/content/darknet


## Evaluation
Now, we will evaluate the trained model.

Optional: We can take the already trained model from Google Drive in order to avoid the training.

Before to test it, we will change the validation dataset from validation file to testing file:

In [0]:
!sed -i 's|valid = /content/darknet/dataset/acfr-fruit-dataset/almonds/val.txt|valid = /content/darknet/dataset/acfr-fruit-dataset/almonds/test.txt|g' dataset/almond.data
!sed -i 's|valid = /content/darknet/dataset/acfr-fruit-dataset/apples/val.txt|valid = /content/darknet/dataset/acfr-fruit-dataset/apples/test.txt|g' dataset/apple.data
!sed -i 's|valid = /content/darknet/dataset/acfr-fruit-dataset/mangoes/val.txt|valid = /content/darknet/dataset/acfr-fruit-dataset/mangoes/test.txt|g' dataset/mango.data
!sed -i 's|valid = /content/darknet/dataset/VOCDevkit/VOC2007/val.txt|valid = /content/darknet/dataset/VOCDevkit/VOC2007/test.txt|g' dataset/m.data

In [0]:
# WGISD
!./darknet detector map dataset/uva.data dataset/yolov3-voc.cfg /content/models/yolov3-wgisd.weights -iou_thresh 0.3

 CUDA-version: 10010 (10010), cuDNN: 7.6.5, CUDNN_HALF=1, GPU count: 1  
 CUDNN_HALF=1 
 OpenCV version: 3.2.0
 compute_capability = 600, cudnn_half = 0 
net.optimized_memory = 0 
mini_batch = 1, batch = 16, time_steps = 1, train = 0 
   layer   filters  size/strd(dil)      input                output
   0 conv     32       3 x 3/ 1    416 x 416 x   3 ->  416 x 416 x  32 0.299 BF
   1 conv     64       3 x 3/ 2    416 x 416 x  32 ->  208 x 208 x  64 1.595 BF
   2 conv     32       1 x 1/ 1    208 x 208 x  64 ->  208 x 208 x  32 0.177 BF
   3 conv     64       3 x 3/ 1    208 x 208 x  32 ->  208 x 208 x  64 1.595 BF
   4 Shortcut Layer: 1,  wt = 0, wn = 0, outputs: 208 x 208 x  64 0.003 BF
   5 conv    128       3 x 3/ 2    208 x 208 x  64 ->  104 x 104 x 128 1.595 BF
   6 conv     64       1 x 1/ 1    104 x 104 x 128 ->  104 x 104 x  64 0.177 BF
   7 conv    128       3 x 3/ 1    104 x 104 x  64 ->  104 x 104 x 128 1.595 BF
   8 Shortcut Layer: 5,  wt = 0, wn = 0, outputs: 104 x 104 x 

In [0]:
# ACFR Almonds
!./darknet detector map dataset/almond.data dataset/yolov3-voc.cfg /content/models/yolov3-acfr-almond.weights -iou_thresh 0.3

 CUDA-version: 10010 (10010), cuDNN: 7.6.5, CUDNN_HALF=1, GPU count: 1  
 CUDNN_HALF=1 
 OpenCV version: 3.2.0
 0 : compute_capability = 600, cudnn_half = 0, GPU: Tesla P100-PCIE-16GB 
net.optimized_memory = 0 
mini_batch = 1, batch = 16, time_steps = 1, train = 0 
   layer   filters  size/strd(dil)      input                output
   0 conv     32       3 x 3/ 1    416 x 416 x   3 ->  416 x 416 x  32 0.299 BF
   1 conv     64       3 x 3/ 2    416 x 416 x  32 ->  208 x 208 x  64 1.595 BF
   2 conv     32       1 x 1/ 1    208 x 208 x  64 ->  208 x 208 x  32 0.177 BF
   3 conv     64       3 x 3/ 1    208 x 208 x  32 ->  208 x 208 x  64 1.595 BF
   4 Shortcut Layer: 1,  wt = 0, wn = 0, outputs: 208 x 208 x  64 0.003 BF
   5 conv    128       3 x 3/ 2    208 x 208 x  64 ->  104 x 104 x 128 1.595 BF
   6 conv     64       1 x 1/ 1    104 x 104 x 128 ->  104 x 104 x  64 0.177 BF
   7 conv    128       3 x 3/ 1    104 x 104 x  64 ->  104 x 104 x 128 1.595 BF
   8 Shortcut Layer: 5,  wt = 0

In [0]:
# ACFR Apples
!./darknet detector map dataset/apple.data dataset/yolov3-voc.cfg /content/models/yolov3-acfr-apple.weights -iou_thresh 0.3

 CUDA-version: 10010 (10010), cuDNN: 7.6.5, CUDNN_HALF=1, GPU count: 1  
 CUDNN_HALF=1 
 OpenCV version: 3.2.0
 0 : compute_capability = 600, cudnn_half = 0, GPU: Tesla P100-PCIE-16GB 
net.optimized_memory = 0 
mini_batch = 1, batch = 16, time_steps = 1, train = 0 
   layer   filters  size/strd(dil)      input                output
   0 conv     32       3 x 3/ 1    416 x 416 x   3 ->  416 x 416 x  32 0.299 BF
   1 conv     64       3 x 3/ 2    416 x 416 x  32 ->  208 x 208 x  64 1.595 BF
   2 conv     32       1 x 1/ 1    208 x 208 x  64 ->  208 x 208 x  32 0.177 BF
   3 conv     64       3 x 3/ 1    208 x 208 x  32 ->  208 x 208 x  64 1.595 BF
   4 Shortcut Layer: 1,  wt = 0, wn = 0, outputs: 208 x 208 x  64 0.003 BF
   5 conv    128       3 x 3/ 2    208 x 208 x  64 ->  104 x 104 x 128 1.595 BF
   6 conv     64       1 x 1/ 1    104 x 104 x 128 ->  104 x 104 x  64 0.177 BF
   7 conv    128       3 x 3/ 1    104 x 104 x  64 ->  104 x 104 x 128 1.595 BF
   8 Shortcut Layer: 5,  wt = 0

In [0]:
# ACFR Mangoes
!./darknet detector map dataset/mango.data dataset/yolov3-voc.cfg /content/models/yolov3-acfr-mango.weights -iou_thresh 0.3

 CUDA-version: 10010 (10010), cuDNN: 7.6.5, CUDNN_HALF=1, GPU count: 1  
 CUDNN_HALF=1 
 OpenCV version: 3.2.0
 0 : compute_capability = 600, cudnn_half = 0, GPU: Tesla P100-PCIE-16GB 
net.optimized_memory = 0 
mini_batch = 1, batch = 16, time_steps = 1, train = 0 
   layer   filters  size/strd(dil)      input                output
   0 conv     32       3 x 3/ 1    416 x 416 x   3 ->  416 x 416 x  32 0.299 BF
   1 conv     64       3 x 3/ 2    416 x 416 x  32 ->  208 x 208 x  64 1.595 BF
   2 conv     32       1 x 1/ 1    208 x 208 x  64 ->  208 x 208 x  32 0.177 BF
   3 conv     64       3 x 3/ 1    208 x 208 x  32 ->  208 x 208 x  64 1.595 BF
   4 Shortcut Layer: 1,  wt = 0, wn = 0, outputs: 208 x 208 x  64 0.003 BF
   5 conv    128       3 x 3/ 2    208 x 208 x  64 ->  104 x 104 x 128 1.595 BF
   6 conv     64       1 x 1/ 1    104 x 104 x 128 ->  104 x 104 x  64 0.177 BF
   7 conv    128       3 x 3/ 1    104 x 104 x  64 ->  104 x 104 x 128 1.595 BF
   8 Shortcut Layer: 5,  wt = 0

In [40]:
# Mango YOLO
!./darknet detector map dataset/m.data dataset/yolov3-voc.cfg /content/models/yolov3-mango.weights -iou_thresh 0.3

 CUDA-version: 10010 (10010), cuDNN: 7.6.5, CUDNN_HALF=1, GPU count: 1  
 CUDNN_HALF=1 
 OpenCV version: 3.2.0
 0 : compute_capability = 600, cudnn_half = 0, GPU: Tesla P100-PCIE-16GB 
net.optimized_memory = 0 
mini_batch = 1, batch = 16, time_steps = 1, train = 0 
   layer   filters  size/strd(dil)      input                output
   0 conv     32       3 x 3/ 1    416 x 416 x   3 ->  416 x 416 x  32 0.299 BF
   1 conv     64       3 x 3/ 2    416 x 416 x  32 ->  208 x 208 x  64 1.595 BF
   2 conv     32       1 x 1/ 1    208 x 208 x  64 ->  208 x 208 x  32 0.177 BF
   3 conv     64       3 x 3/ 1    208 x 208 x  32 ->  208 x 208 x  64 1.595 BF
   4 Shortcut Layer: 1,  wt = 0, wn = 0, outputs: 208 x 208 x  64 0.003 BF
   5 conv    128       3 x 3/ 2    208 x 208 x  64 ->  104 x 104 x 128 1.595 BF
   6 conv     64       1 x 1/ 1    104 x 104 x 128 ->  104 x 104 x  64 0.177 BF
   7 conv    128       3 x 3/ 1    104 x 104 x  64 ->  104 x 104 x 128 1.595 BF
   8 Shortcut Layer: 5,  wt = 0